# Data Cleaning in python
This practical was based on Section 2 of "An Introduction ot data cleaning with R" from Statistics Netherlands, and adapted for python.
* Available at https://cran.r-project.org/doc/contrib/de_Jonge+van_der_Loo-Introduction_to_data_cleaning_with_R.pdf

## Logging in and getting started

* Open a terminal window and run the following commands:

```
# Login
ssh username@login.rdf.ac.uk
# Load python modules
module load python
module load anaconda
# Create working directory
mkdir dataCleaning
cd dataCleaning
# Create and start editing unnamed.txt
nano unnamed.txt
```

# Part 1: Read csv data into a data frame
Start with a file called unnamed.txt containing the following text:
```
21,6.0 
42,5.9 
18,5.7* 
21,NA
```
Save and close the file.
### Start Python
Run the command:
```
ipython
```

### read_csv
* Import the pandas module as pd
* Read this with pd.read_csv()
 - What has happened to the first row? - it's a header.


In [107]:
import pandas as pd
pd.read_csv("unnamed.txt")

21   6.0
0  42   5.9
1  18  5.7*
2  21   NaN

### Header row
* Read this again with header=None as an argument
 - What has happened now? 


In [108]:
pd.read_csv("unnamed.txt", header=None)

0     1
0  21   6.0
1  42   5.9
2  18  5.7*
3  21   NaN

### Setting the column names

In [109]:
pd.read_csv("unnamed.txt", header=None, names=('age','height'))

age height
0   21    6.0
1   42    5.9
2   18   5.7*
3   21    NaN

In [110]:
person = pd.read_csv("unnamed.txt", header=None, names=('age','height'))
person

age height
0   21    6.0
1   42    5.9
2   18   5.7*
3   21    NaN

In [97]:
person.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4 entries, 0 to 3
Data columns (total 2 columns):
age       4 non-null int64
height    3 non-null object
dtypes: int64(1), object(1)
memory usage: 96.0+ bytes


* Let’s convert the height column into numeric values
What happened to 5.7*?

In [100]:
person.height = person.height.convert_objects(convert_numeric=True) 
person

age  height
0   21     6.0
1   42     5.9
2   18     NaN
3   21     NaN

In [101]:
person.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4 entries, 0 to 3
Data columns (total 2 columns):
age       4 non-null int64
height    2 non-null float64
dtypes: float64(1), int64(1)
memory usage: 96.0 bytes


In [102]:
person

age  height
0   21     6.0
1   42     5.9
2   18     NaN
3   21     NaN

# Part 2 Dealing with unstructured data
## Step 1 Readlines

In [10]:
with open("daltons.txt") as f:
    txt = f.readlines()

In [11]:
txt

['%% Data on the Dalton Brothers\r\n',
 'Gratt,1861,1892\r\n',
 'Bob,1892\r\n',
 '1871,Emmet,1937\r\n',
 '% Names, birth and death dates\r\n']

### Pattern matching

In [12]:
iris = pd.read_csv('https://github.com/pandas-dev/pandas/raw/master/pandas/tests/data/iris.csv')

In [13]:
iris.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 150 entries, 0 to 149
Data columns (total 5 columns):
SepalLength    150 non-null float64
SepalWidth     150 non-null float64
PetalLength    150 non-null float64
PetalWidth     150 non-null float64
Name           150 non-null object
dtypes: float64(4), object(1)
memory usage: 7.0+ KB


In [14]:
names = iris.columns.tolist()  # Alternatively list(iris)

In [15]:
names

['SepalLength', 'SepalWidth', 'PetalLength', 'PetalWidth', 'Name']

#### Using list comprehension

* Python's list comprehension applys a function to each element in a list.

In [16]:
numbers = [4,5,6]
[x*2 for x in numbers]

[8, 10, 12]

In [17]:
'Petal' in 'PetalLength'

True

In [18]:
["Petal" in name for name in names]

[False, False, True, True, False]

In [19]:
[name for name in names if 'Petal' in name]

['PetalLength', 'PetalWidth']

#### Regular expressions
* As above, using regular expressions

In [20]:
import re
[name for name in names if re.search("Petal", name)]

['PetalLength', 'PetalWidth']

• ^ matches pattern at start

In [21]:
[name for name in names if re.search("^P", name)]

['PetalLength', 'PetalWidth']

• $ matches pattern at end

In [22]:
[name for name in names if re.search("th$", name)]

['SepalLength', 'SepalWidth', 'PetalLength', 'PetalWidth']

• [] character class, match characters enclosed in []

In [126]:
[name for name in names if re.search("[g][t][h]", name)]


['SepalLength', 'PetalLength']

For more see help(re) for full explanation.

### An aside on Simple string matching alternatives (regular expression are more powerful, and return position of match)

In [24]:
[name for name in names if name.startswith("P")]

['PetalLength', 'PetalWidth']

In [25]:
[name.startswith("P") for name in names]

[False, False, True, True, False]

In [26]:
[name for name in names if name.endswith("th")]

['SepalLength', 'SepalWidth', 'PetalLength', 'PetalWidth']

In [27]:
[name for name in names if "gth" in name]

['SepalLength', 'PetalLength']

### Subsetting and Logicals

* Logical AND &

In [28]:
iris[(iris.Name == "Iris-versicolor") & (iris.PetalWidth >= 1.7)]

SepalLength  SepalWidth  PetalLength  PetalWidth             Name
70          5.9         3.2          4.8         1.8  Iris-versicolor
77          6.7         3.0          5.0         1.7  Iris-versicolor

* Logical OR |

In [29]:
iris[(iris.SepalLength == 4.3) | (iris.SepalLength == 7.9)]

SepalLength  SepalWidth  PetalLength  PetalWidth            Name
13           4.3         3.0          1.1         0.1     Iris-setosa
131          7.9         3.8          6.4         2.0  Iris-virginica

* Note == for comparison not =

* Logical NOT ~

In [30]:
iris[~(iris.SepalLength > 4.3)]

SepalLength  SepalWidth  PetalLength  PetalWidth         Name
13          4.3           3          1.1         0.1  Iris-setosa

### Selecting rows and columns

* Pandas filter() command selects columns
* Can filter by regular expression

In [31]:
iris.filter(regex='^P').columns

Index([u'PetalLength', u'PetalWidth'], dtype='object')

* Select columns and rows at the same time

In [32]:
iris.filter(regex='^P')[~(iris.SepalLength > 4.3)]

PetalLength  PetalWidth
13          1.1         0.1

## Step 2 (cont) Selecting lines only with data

Find lines starting with a % sign

In [33]:
[name for name in txt if re.search("^%", name)]


['%% Data on the Dalton Brothers\r\n', '% Names, birth and death dates\r\n']

In [34]:
dat = [name for name in txt if not re.search("^%", name)]
dat

['Gratt,1861,1892\r\n', 'Bob,1892\r\n', '1871,Emmet,1937\r\n']

## Step 3 - split lines into fields

* For each line, we now want to extract the content for each field.
* We now need to know about splitting lines and learn about lists in Python.

In [35]:
L = [1,2, "three", [3,3]]

[] retrieves an object from the list.
Indexing starts at zero.

In [36]:
L[0]

1

Can select a range of values

In [37]:
L[0:3]

[1, 2, 'three']

Use - to count from end
e.g. last 2 items

In [38]:
L[-2]

'three'

In [39]:
L[-2:]

['three', [3, 3]]

### split
split() splits a string into a list of substrings at the point indicated by the split pattern.

In [40]:
x = "Split the words in a sentence\n"
x.split(" ")

['Split', 'the', 'words', 'in', 'a', 'sentence\n']

* Use split() to split each line into data chunks.
* Use strip() to remove whitespace characters such as \n

In [41]:
x.strip().split(" ")

['Split', 'the', 'words', 'in', 'a', 'sentence']

In [42]:
field_list = [ln.strip().split(",") for ln in dat]
field_list

[['Gratt', '1861', '1892'], ['Bob', '1892'], ['1871', 'Emmet', '1937']]

## Step 4 - Standardise Rows

* Now we want to make sure each row has the same number of fields and in the same order.
* Let's write a function to process each row.

## User-defined function in Python

`def my_function(arg1, arg2, ...):
    statements
    return object
code not in my_function`

* Objects in the function are local to the function.
* The object returned can be any data type
* Functions are stored as objects
* An explicit return statement is required.
* : marks the start of the body of the function. The body must be indented, the end of the indentation marks the end of the function.
****
* So let's write a function that takes the list representing each line, extracts the person's name, their birth and death dates and re-orders them accordingly.
* Let's call this function assign_fields and store it in a file called assign_fields.py

* Exit ipython by typing:
    `exit()`
* Open a text file with:
    `nano assign_fields.py`

In [115]:
import pandas as pd
def assign_fields(x):
    # x is a list of words from a line.
    
    # create a list to hold the extracted fields, initialised to 'NA' by default.
    out = ['NA'] * 3
    
    for word in x:
        # extract the name value (alphabetical) and insert in the first position.
        if word.isalpha():
            out[0] = word
        else:    
            # extract birth date (if any)
            # based on knowledge that all Dalton brothers were born before 1890
            # and died after 1890
            if (int(word) < 1890): 
                out[1] = word
            elif (int(word) > 1890): 
                out[2] = word
    # Returns a list format: [name, born, died]            
    return out

* Save the assign_fields.py file and restart ipython.

* Read the file in again after re-starting ipython

In [127]:
import pandas as pd
import re
with open("daltons.txt") as f:
    txt = f.readlines()
dat = [name for name in txt if not re.search("^%", name)]
field_list = [ln.strip().split(",") for ln in dat]

* From the assign_fields module file, import the assign_fields function.
* Run the assign_fields function over every row in the list of fields

In [129]:
from assign_fields import assign_fields
standard_fields = [assign_fields(ln) for ln in field_list]
standard_fields

[['Gratt', '1861', '1892'], ['Bob', 'NA', '1892'], ['Emmet', '1871', '1937']]

## Step 5 - Transform to a data frame

* Let's convert the list of standardised rows into a data frame.

In [47]:
daltons = pd.DataFrame(standard_fields)

In [48]:
daltons

0     1     2
0  Gratt  1861  1892
1    Bob    NA  1892
2  Emmet  1871  1937

In [49]:
daltons = pd.DataFrame(standard_fields, columns=['name','birth','death'])

In [50]:
daltons

name birth death
0  Gratt  1861  1892
1    Bob    NA  1892
2  Emmet  1871  1937

## Step 6 - Normalise and coerce to correct type

* Now need to coerce our columns to the correct types e.g. numerics, characters, categories, ... In this case birth and death, need to be numerics.

In [51]:
daltons.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3 entries, 0 to 2
Data columns (total 3 columns):
name     3 non-null object
birth    3 non-null object
death    3 non-null object
dtypes: object(3)
memory usage: 96.0+ bytes


In [78]:
daltons.birth = daltons.birth.convert_objects(convert_numeric=True)

In [79]:
daltons.death = daltons.death.convert_objects(convert_numeric=True)

In [80]:
daltons

name  birth  death
0  Gratt   1861   1892
1    Bob    NaN   1892
2  Emmet   1871   1937

In [81]:
daltons.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3 entries, 0 to 2
Data columns (total 3 columns):
name     3 non-null object
birth    2 non-null float64
death    3 non-null int64
dtypes: float64(1), int64(1), object(1)
memory usage: 96.0+ bytes


* The birth column contains floats instead of integers because you can't mix int and NaN data types in pandas.

### Repeatability

* Storing the instructions in a file along **with comments** enables repetablility. 
* Remember to import the required modules.
* Ipython notebooks allow nicely formatted comments, code, and output to be mixed.

In [134]:
import pandas as pd
import re
with open("daltons.txt") as f:
    txt = f.readlines()
dat = [name for name in txt if not re.search("^%", name)]
field_list = [ln.strip().split(",") for ln in dat]
from assign_fields import assign_fields
standard_fields = [assign_fields(ln) for ln in field_list]
colnames = ['name', 'birth', 'death']
daltons = pd.DataFrame(standard_fields, columns=colnames)
daltons.birth = daltons.birth.convert_objects(convert_numeric=True) 
daltons.death = daltons.death.convert_objects(convert_numeric=True)
print("Daltons")
print(daltons)
print('\nInfo')
print(daltons.info())

Daltons
    name  birth  death
0  Gratt   1861   1892
1    Bob    NaN   1892
2  Emmet   1871   1937

Info
<class 'pandas.core.frame.DataFrame'>
Int64Index: 3 entries, 0 to 2
Data columns (total 3 columns):
name     3 non-null object
birth    2 non-null float64
death    3 non-null int64
dtypes: float64(1), int64(1), object(1)
memory usage: 96.0+ bytes
None


### Fixing character vectors - re.sub

In [83]:
import re
import pandas as pd
string = "Replace the spaces in this text"
re.sub(" ", "-", string)

'Replace-the-spaces-in-this-text'

In [84]:
string = "Replace first space in this text"
re.sub(" ", "-", string, count=1)

'Replace-first space in this text'

In [85]:
iris = pd.read_csv('https://github.com/pandas-dev/pandas/raw/master/pandas/tests/data/iris.csv')

In [86]:
names = iris.columns.tolist()

In [87]:
names

['SepalLength', 'SepalWidth', 'PetalLength', 'PetalWidth', 'Name']

In [62]:
[re.sub("e", '-', name) for name in names]

['S-palL-ngth', 'S-palWidth', 'P-talL-ngth', 'P-talWidth', 'Nam-']

# Parallel processing in Python


Serial code:

Parallel code using 'multiprocessing' module

In [133]:
import multiprocessing
from multiprocessing import Pool

try:
    cpus = multiprocessing.cpu_count()
except NotImplementedError:
    cpus = 2   # arbitrary default

pool = Pool(processes=cpus)
pool.map(assign_fields, field_list)

[['Gratt', '1861', '1892'], ['Bob', 'NA', '1892'], ['Emmet', '1871', '1937']]